In [1]:
# Here are a set of libraries we imported to complete this assignment. 
# Feel free to use these or equivalent libraries for your implementation
# If you can run this cell without any errors, you're ready to go.
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import matplotlib.pyplot as plt # this is used for the plot the graph 

import seaborn as sns # used for plot interactive graph.
from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV
from sklearn import metrics
from sklearn.svm import SVC  
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.cluster import KMeans
from sklearn.metrics import confusion_matrix
import sklearn.metrics.cluster as smc
from matplotlib import pyplot

from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score
from sklearn.metrics import f1_score

from sklearn.metrics import roc_curve, auc

from sklearn.naive_bayes import GaussianNB


# scikit-learn k-fold cross-validation
from numpy import array
from sklearn.model_selection import KFold


import os
import itertools
import random 

%matplotlib inline

random.seed(148) 

In [ ]:
# make it dark mode (delete it later)
# !jt -l
# jt -l

In [3]:
#!jt -t <theme name>
#!jt -t chesterish
#jt -t chesterish

In [4]:
#Enable the toolbar: !jt -t [theme name] -T

In [3]:
# Helper function allowing you to export a graph
def save_fig(fig_id, tight_layout=True, fig_extension="png", resolution=300):
    path = os.path.join(fig_id + "." + fig_extension)
    print("Saving figure", fig_id)
    if tight_layout:
        plt.tight_layout()
    plt.savefig(path, format=fig_extension, dpi=resolution)

In [4]:
# Helper function that allows you to draw nicely formatted confusion matrices
def draw_confusion_matrix(y, yhat, classes):
    '''
        Draws a confusion matrix for the given target and predictions
        Adapted from scikit-learn example.
    '''
    plt.cla()
    plt.clf()
    matrix = confusion_matrix(y, yhat)
    plt.imshow(matrix, interpolation='nearest', cmap=plt.cm.Blues)
    plt.title("Confusion Matrix")
    plt.colorbar()
    num_classes = len(classes)
    plt.xticks(np.arange(num_classes), classes, rotation=90)
    plt.yticks(np.arange(num_classes), classes)
    
    fmt = 'd'
    thresh = matrix.max() / 2.
    for i, j in itertools.product(range(matrix.shape[0]), range(matrix.shape[1])):
        plt.text(j, i, format(matrix[i, j], fmt),
                 horizontalalignment="center",
                 color="white" if matrix[i, j] > thresh else "black")

    plt.ylabel('True label')
    plt.xlabel('Predicted label')
    plt.tight_layout()
    plt.show()

1. Merge Datasets and Effectively Link information - Useful information for this project will come from disparate datasets. You will need to effectively merge them into a single dataframe for analysis

Can combine:
Brand Average Retail Price
Brand total sales
Brand total units

Combine on: Brand and Month to get the columns:
Brand, Month:
    ARP, vs Prior Period (Average Retail Price), Total Sales (total sales), Total Units, vs Prior Period (total units)

In [5]:
#data_1 = pd.read_csv('data\BrandAverageRetailPrice.csv')
#data_2 = pd.read_csv('data\BrandDetails.csv')
#data_3 = pd.read_csv('data\BrandTotalSales.csv')
#data_4 = pd.read_csv('data\BrandTotalUnits.csv')

#combine based on brand
#https://jakevdp.github.io/PythonDataScienceHandbook/03.07-merge-and-join.html
#df3 = pd.merge(df1, df2)
#combine_1 = pd.merge(data_1, data_2)
#combine_2 = pd.merge(data_3, data_4)
#data = pd.merge(combine_1, combine_2)

#to check all of data
#data.to_csv('total_combine_data.csv', index=False)

In [6]:
#the , in the thousands space makes the columns an object
data_1 = pd.read_csv('data\BrandAverageRetailPrice.csv', thousands=",")
data_2 = pd.read_csv('data\BrandDetails.csv')
data_3 = pd.read_csv('data\BrandTotalSales.csv', thousands=",")
data_4 = pd.read_csv('data\BrandTotalUnits.csv', thousands=",")
#Need to rename prior period as it is not being added onto, they are being combined (in 1 and 4)
data_4 = data_4.rename(columns={"vs. Prior Period": "vs Prior Period unit"})

#combine based on brand
#https://jakevdp.github.io/PythonDataScienceHandbook/03.07-merge-and-join.html
#df3 = pd.merge(df1, df2)
#Need outer join to keep every month
#Difference between price and unit # in prior period
combine_1 = pd.merge(data_1, data_4, how='left', suffixes=('_apr', '_units'))
#combine_2 = pd.merge(data_3, data_4)
data_per_month = pd.merge(combine_1, data_3, left_on = ['Brands', 'Months'], right_on = ['Brand', 'Months'], how= 'left', \
                          suffixes=(False, '_total_sales'))

#brand got copied over onto another column, need to delete that
del data_per_month['Brand']

#to check all of data
data_per_month.to_csv('data_per_month.csv', index=False)

Need to handle BrandDetails differents as it only tracks their items and their price and then details the Total Sales, Total Units, ARP

Note for later: flavor, is flavored == Null, ask later

In [7]:
#Do later as it does not fit at the moment

In [8]:
#Head Method
data_per_month.head()
#arp is average retail price

Brands   Months        ARP  vs. Prior Period  Total Units  \
0  #BlackSeries  08/2020  15.684913               NaN  1616.339004   
1  #BlackSeries  09/2020        NaN         -1.000000          NaN   
2  #BlackSeries  01/2021  13.611428               NaN   715.532838   
3  #BlackSeries  02/2021  11.873182         -0.127705   766.669135   
4  #BlackSeries  03/2021        NaN         -1.000000          NaN   

   vs Prior Period unit  Total Sales ($)  
0                   NaN     25352.135918  
1             -1.000000              NaN  
2                   NaN      9739.423400  
3              0.071466      9102.802187  
4             -1.000000              NaN

In [9]:
#Describe Method
data_per_month.describe()

ARP  vs. Prior Period   Total Units  vs Prior Period unit  \
count  25279.000000      24499.000000  2.527900e+04          24893.000000   
mean      22.679732         -0.065028  2.886210e+04              0.267441   
std       19.802724          0.388923  1.617156e+05              3.293738   
min        0.000000         -1.000000  3.842953e+00             -1.000000   
25%       10.512827         -0.088073  7.169135e+02             -0.349745   
50%       17.033051         -0.011649  3.605059e+03             -0.054400   
75%       31.505612          0.045232  1.564044e+04              0.241073   
max      700.874984         12.645741  5.248082e+06            250.792020   

       Total Sales ($)  
count     2.527900e+04  
mean      4.093729e+05  
std       1.596024e+06  
min       0.000000e+00  
25%       1.390320e+04  
50%       6.210080e+04  
75%       2.473270e+05  
max       4.036351e+07

In [10]:
#Info method
data_per_month.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 27211 entries, 0 to 27210
Data columns (total 7 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   Brands                27211 non-null  object 
 1   Months                27211 non-null  object 
 2   ARP                   25279 non-null  float64
 3   vs. Prior Period      24499 non-null  float64
 4   Total Units           25279 non-null  float64
 5   vs Prior Period unit  24893 non-null  float64
 6   Total Sales ($)       25279 non-null  float64
dtypes: float64(5), object(2)
memory usage: 1.7+ MB


2. Develop basic Time Series Feature Extraction Plan - develop a series of standard timeseries features to augment your dataset and enable timeseries predictive models.

In [11]:
#Need to split the data before we add on the features:
#Everything but the last month of a brand = train
#Last month of each brand = test

#only input the averages into the training set not the test set
#as to not leak values from the test to train and get overfitting

#https://stackoverflow.com/questions/36923494/pandas-dataframe-use-previous-row-value-for-complicated-if-conditions-to-deter

test_data = []
train_data = []

d = {'Brands': [], 'Months': [], 'ARP': [], 'vs. Prior Period': [], 'Total Units': [], 'vs Prior Period unit': [], 'Total Sales ($)': []}
test_data = pd.DataFrame(data=d)
train_data = pd.DataFrame(data=d)

print(test_data)
print(train_data)
print(data_per_month)

for index, row in data_per_month.iterrows():
    #row = dict containing all data for that row, not row number
    #that would be index
    next_row = index + 1
    #need .iloc
    if (next_row >= len(data_per_month)):
        #Need to check to see if any of the items are null, if they are, add in the averges
        
        test_data = test_data.append(data_per_month.iloc[index])
    elif (data_per_month.iloc[next_row]['Brands'] != data_per_month.iloc[index]['Brands']):
        test_data = test_data.append(data_per_month.iloc[index])
    else:
        train_data = train_data.append(data_per_month.iloc[index])

#print(train_data)
#print(test_data)
#to check all of data
train_data.to_csv('train_data_per_month.csv', index=False)
test_data.to_csv('test_data_per_month.csv', index=False)

Empty DataFrame
Columns: [Brands, Months, ARP, vs. Prior Period, Total Units, vs Prior Period unit, Total Sales ($)]
Index: []
Empty DataFrame
Columns: [Brands, Months, ARP, vs. Prior Period, Total Units, vs Prior Period unit, Total Sales ($)]
Index: []
              Brands   Months        ARP  vs. Prior Period  Total Units  \
0       #BlackSeries  08/2020  15.684913               NaN  1616.339004   
1       #BlackSeries  09/2020        NaN         -1.000000          NaN   
2       #BlackSeries  01/2021  13.611428               NaN   715.532838   
3       #BlackSeries  02/2021  11.873182         -0.127705   766.669135   
4       #BlackSeries  03/2021        NaN         -1.000000          NaN   
...              ...      ...        ...               ...          ...   
27206  Zuma Topicals  08/2019  31.598214               NaN   312.515336   
27207  Zuma Topicals  09/2019  37.860964          0.198199   464.306316   
27208  Zuma Topicals  10/2019  34.546154         -0.087552   348.057905

In [12]:
#Now, need to add in missing values to test data
#Columns:
#0: Brand
#1: Months
#2: ARP
#3: vs. Prior Period
#4: Total Units
#5: vs Prior Period unit
#6: Total Sales ($)

#Need the () for copy!!
filled_in_test_data = test_data.copy().reset_index()

# d = {'Brands': [], 'Months': [], 'ARP': [], 'vs. Prior Period': [], 'Total Units': [], 'vs Prior Period unit': [], 'Total Sales ($)': []}
# filled_in_test_data = pd.DataFrame(data=d)

#project 1

#Taking the average as it feels better

new_ARP = data_per_month["ARP"].mean()
new_vs_Prior_Period = data_per_month["vs. Prior Period"].mean()
new_total_units = data_per_month["Total Units"].mean()
new_vs_unit = data_per_month["vs Prior Period unit"].mean()
new_total_sales = data_per_month["Total Sales ($)"].mean()

filled_in_test_data["ARP"].fillna(new_ARP, inplace=True)
#to replace the -1's
#Don't replace the -1's!!!
#filled_in_test_data["ARP"].replace({-1: new_ARP}, inplace=True)

filled_in_test_data["vs. Prior Period"].fillna(new_vs_Prior_Period, inplace=True)
#filled_in_test_data["vs. Prior Period"].replace({-1: new_vs_Prior_Period}, inplace=True)

filled_in_test_data["Total Units"].fillna(new_total_units, inplace=True)
#filled_in_test_data["Total Units"].replace({-1: new_total_units}, inplace=True)

filled_in_test_data["vs Prior Period unit"].fillna(new_vs_unit, inplace=True)
#filled_in_test_data["vs Prior Period unit"].replace({-1: new_vs_unit}, inplace=True)

filled_in_test_data["Total Sales ($)"].fillna(new_total_sales, inplace=True)
#filled_in_test_data["Total Sales ($)"].replace({-1: new_total_sales}, inplace=True)

        
filled_in_test_data.to_csv('filled_in_test_data.csv', index=False)

In [13]:
#now add in missing values to Train data, but leave out the test data
#Columns:
#0: Brand
#1: Months
#2: ARP
#3: vs. Prior Period
#4: Total Units
#5: vs Prior Period unit
#6: Total Sales ($)

#Need the () for copy!!
filled_in_train_data = train_data.copy().reset_index()

# d = {'Brands': [], 'Months': [], 'ARP': [], 'vs. Prior Period': [], 'Total Units': [], 'vs Prior Period unit': [], 'Total Sales ($)': []}
# filled_in_test_data = pd.DataFrame(data=d)

#project 1

new_ARP = test_data["ARP"].mean()
new_vs_Prior_Period = test_data["vs. Prior Period"].mean()
new_total_units = test_data["Total Units"].mean()
new_vs_unit = test_data["vs Prior Period unit"].mean()
new_total_sales = test_data["Total Sales ($)"].mean()

filled_in_train_data["ARP"].fillna(new_ARP, inplace=True)
#to replace the -1's
#don't replace the -1's!!
#filled_in_train_data["ARP"].replace({-1: new_ARP}, inplace=True)

filled_in_train_data["vs. Prior Period"].fillna(new_vs_Prior_Period, inplace=True)
#filled_in_train_data["vs. Prior Period"].replace({-1: new_vs_Prior_Period}, inplace=True)

filled_in_train_data["Total Units"].fillna(new_total_units, inplace=True)
#filled_in_train_data["Total Units"].replace({-1: new_total_units}, inplace=True)

filled_in_train_data["vs Prior Period unit"].fillna(new_vs_unit, inplace=True)
#filled_in_train_data["vs Prior Period unit"].replace({-1: new_vs_unit}, inplace=True)

filled_in_train_data["Total Sales ($)"].fillna(new_total_sales, inplace=True)
#filled_in_train_data["Total Sales ($)"].replace({-1: new_total_sales}, inplace=True)

        
filled_in_train_data.to_csv('filled_in_train_data.csv', index=False)

Last months, 
Last quarter's, 
Last year's average

In [97]:
train_copy = train_data.copy().reset_index()
# train_copy.dropna(subset=['Months'], inplace=True)

row is: 
0
index is
Brands                  #BlackSeries
Months                       08/2020
ARP                        15.684913
vs. Prior Period           -0.525658
Total Units              1616.339004
vs Prior Period unit       -0.421739
Total Sales ($)         25352.135918
Name: 0, dtype: object
index [1] is
08/2020
index[1][0] is
B
index[0][1] is
0
index[Month] is:
08/2020
index[Months].split('/') is
['08', '2020']
08
2020
Previous row is 0
before_previous_month
7
2020
7/2020
row is: 
1
index is
Brands                   #BlackSeries
Months                        09/2020
ARP                         19.621934
vs. Prior Period                 -1.0
Total Units              28690.238607
vs Prior Period unit             -1.0
Total Sales ($)         378071.185836
Name: 1, dtype: object
index [1] is
09/2020
index[1][0] is
B
index[0][1] is
0
index[Month] is:
09/2020
index[Months].split('/') is
['09', '2020']
09
2020


IndexError: single positional indexer is out-of-bounds

In [98]:
# https://www.geeksforgeeks.org/split-a-text-column-into-two-columns-in-pandas-dataframe/
# train_data.Months.str.split('/')[1]
# train_copy['month'], train_copy['year'] = pd.DataFrame(train_data.Months.str.split('/',1).tolist(), columns = ['month', 'year'])
# train_copy
train_2 = pd.DataFrame(train_data.Months.str.split('/', 1).tolist(), columns = ['month', 'year'])
train_copy['month'] = train_2['month']
train_copy['year'] = train_2['year']
train_copy

index            Brands   Months        ARP  vs. Prior Period  \
0          0      #BlackSeries  08/2020  15.684913               NaN   
1          1      #BlackSeries  09/2020        NaN         -1.000000   
2          2      #BlackSeries  01/2021  13.611428               NaN   
3          3      #BlackSeries  02/2021  11.873182         -0.127705   
4          5  101 Cannabis Co.  11/2019  34.066667               NaN   
...      ...               ...      ...        ...               ...   
25579  27204              Zoma  08/2020   9.220357          0.224096   
25580  27206     Zuma Topicals  08/2019  31.598214               NaN   
25581  27207     Zuma Topicals  09/2019  37.860964          0.198199   
25582  27208     Zuma Topicals  10/2019  34.546154         -0.087552   
25583  27209     Zuma Topicals  11/2019  36.850000          0.066689   

       Total Units  vs Prior Period unit  Total Sales ($) month  year  
0      1616.339004                   NaN     25352.135918    08  2020  
1              NaN             -1.000000              NaN    09  2020  
2       715.532838                   NaN      9739.423400    01  2021  
3       766.669135              0.071466      9102.802187    02  2021  
4       131.067720                   NaN      4465.040321    11  2019  
...            ...                   ...              ...   ...   ...  
25579   604.238880             -0.636775      5571.298054    08  2020  
25580   312.515336                   NaN      9874.926545    08  2019  
25581   464.306316              0.485707     17579.084649    09  2019  
25582   348.057905             -0.250370     12024.061922    10  2019  
25583   135.922080             -0.609484      5008.728648    11  2019  

[25584 rows x 10 columns]

In [107]:
train_copy.dropna(subset=['ARP'], inplace=True)
if 'index' in train_copy.columns:
    train_copy.drop(['index'], axis=1, inplace=True)

# yearly average: count brands and year, then add sum of ARP, then divide
grouped = train_copy.groupby(['Brands', 'year'])
train_copy['annual_avg'] = grouped['ARP'].transform('sum') / grouped['Brands'].transform('count')
train_copy

Brands   Months        ARP  vs. Prior Period  Total Units  \
0          #BlackSeries  08/2020  15.684913               NaN  1616.339004   
2          #BlackSeries  01/2021  13.611428               NaN   715.532838   
3          #BlackSeries  02/2021  11.873182         -0.127705   766.669135   
4      101 Cannabis Co.  11/2019  34.066667               NaN   131.067720   
6      101 Cannabis Co.  01/2020  34.134929               NaN   345.413448   
...                 ...      ...        ...               ...          ...   
25579              Zoma  08/2020   9.220357          0.224096   604.238880   
25580     Zuma Topicals  08/2019  31.598214               NaN   312.515336   
25581     Zuma Topicals  09/2019  37.860964          0.198199   464.306316   
25582     Zuma Topicals  10/2019  34.546154         -0.087552   348.057905   
25583     Zuma Topicals  11/2019  36.850000          0.066689   135.922080   

       vs Prior Period unit  Total Sales ($) month  year  annual_avg  
0                       NaN     25352.135918    08  2020   15.684913  
2                       NaN      9739.423400    01  2021   12.742305  
3                  0.071466      9102.802187    02  2021   12.742305  
4                       NaN      4465.040321    11  2019   34.066667  
6                       NaN     11790.663567    01  2020   32.619525  
...                     ...              ...   ...   ...         ...  
25579             -0.636775      5571.298054    08  2020    8.376369  
25580                   NaN      9874.926545    08  2019   35.213833  
25581              0.485707     17579.084649    09  2019   35.213833  
25582             -0.250370     12024.061922    10  2019   35.213833  
25583             -0.609484      5008.728648    11  2019   35.213833  

[24502 rows x 10 columns]

In [63]:
# Austyn
# #Last months
# #Last quarter's 
# #Last year's average

# #Last months:
# months = ['Jan', 'Feb', 'March', 'Apr', "May", 'Jun', 'Jul', 'Aug', 'Sept', 'Oct', 'Nov', 'Dec']
# months_num = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12]

# #augmenting based on vs Prior Period
# #For total sales: divd based on Total Units or ARP, figure out later
# #For each row, 
# #if the row above does not have a month prior, add in a month 
# #add in a check like a column that sayss added in and mark it yes

# #New dataset
# additional_month_train = []

train_filled_in_copy = filled_in_train_data.copy().reset_index()

for row, index in train_filled_in_copy.iterrows():
    #index = dict containing all data for that row, 
    #not row number that would be row
    print("row is: ")
    print(row)
    print("index is")
    print(index)
#     print("index [1] is")
#     print(index[1])
#     print("index[1][0] is")
#     print(index[0][1])
#     print("index[0][1] is")
#     print(index[1][0])
#     print("index[Month] is:")
#     print(index["Months"])
#     #Need string for columns, not indiviual cells
#     print("index[Months].split('/') is")
#     print(index["Months"].split('/'))
#     broken_apart_month = index["Months"].split('/')
#     print(broken_apart_month[0])
#     print(broken_apart_month[1])
    
    
    prev_row = row - 1
    #need .iloc
    if (prev_row < 0):
        # print("Previous row is 0")
        # Need to check to see if any of the items are null, if they are, add in the averges
        # 0th row (the month we are adding before the first row in the dataset)
        new_brand = train_filled_in_copy.iloc[0]['Brands']
        broken_apart_month = index["Months"].split('/')
        previous_month = str(int(broken_apart_month[0])- 1)
        # print("before_previous_month")
        # print(previous_month)
        year = broken_apart_month[1]
        #print(year)
        if (previous_month == 0):
            previous_month = str(12)
            year = str(int(broken_apart_month[1]) - 1)
        combined_previous_month = previous_month + "/" + year
        # print(combined_previous_month)
        
        
        original_arp = float(index["ARP"])
        #print("Original arp is")
        #print(original_arp)
        #new_vs_Prior_Period = data_per_month["vs. Prior Period"].mean()
        new_vs_prior_period = data_per_month["vs. Prior Period"].mean()
        #print("old prior period is")
        #print(index["vs. Prior Period"])
        how_much_new = float(original_arp) * float(index["vs. Prior Period"])
        #print("how much new")
        #print(how_much_new)
        before_arp_int = float(original_arp) + float(how_much_new)
        new_arp = before_arp_int
        #print("new_arp")
        #print(new_arp)
        
        
        original_total_units = float(index["Total Units"])
        new_prior_units = data_per_month["vs Prior Period unit"].mean()
        how_much_new = float(original_total_units) * float(index["vs Prior Period unit"])
        new_total_units_int = float(original_total_units) + float(how_much_new)
        new_total_units = new_total_units_int
        
        
        new_total_sales = new_arp * new_total_units
        
        #new_vs_unit = data_per_month["vs Prior Period unit"].mean()
        additional_month_train = additional_month_train.append([new_brand,
                                                               combined_previous_month,
                                                               new_arp, 
                                                               new_vs_prior_period, 
                                                               new_total_units,
                                                               new_prior_units,
                                                               new_total_sales])
        #supposed to be:
        #Brand: #Black Series
        #Months: 7/2020
        #ARP: 6.75
        #vs. Prior Period: 
        #Total Units: 934
        #vs Prior Period unit:
        #Total Sales ($): 6304.5
        print("New row values are:")
        print("Brand is:")
        print(new_brand)
        print("New month is")
        print(combined_previous_month)
        print("ARP is")
        print(new_arp)
        print("new prior period is")
        print(new_vs_prior_period)
        print("new total units is")
        print(new_total_units)
        print("New prior units are:")
        print(new_prior_units)
        print("new total sales are")
        print(new_total_sales)
        #1st row
        additional_month_train = additional_month_train.append(train_filled_in_copy.iloc[row])
        print("Original row is:")
        print(additional_month_train)
        
        print("---------------------------------------------------------------------------")
        
        
    #If the previous entry does not have the same brand or the months are not 1 apart
    #data_per_month.iloc[next_row]['Brands'] != data_per_month.iloc[index]['Brands']
    elif ((str(train_filled_in_copy.iloc[prev_row]['Brands']) !=
          str(train_filled_in_copy.iloc[row]['Brands'])) or 
          (train_filled_in_copy.iloc[row]['Months'].split('/')[0] != 
           str(int(train_filled_in_copy.iloc[prev_row]['Months'].split('/')[0]) - 1))):
        new_brand = filled_in_train_data.iloc[row]['Brands']
        broken_apart_month = index["Months"].split('/')
        previous_month = str(int(broken_apart_month[0])- 1)
        year = broken_apart_month[1]
        if (previous_month == 0):
            previous_month = str(12)
            year = str(int(broken_apart_month[1]) - 1)
        combined_previous_month = previous_month + "/" + year
        original_arp = float(index["ARP"])
        new_vs_prior_period = data_per_month["vs. Prior Period"].mean()
        how_much_new = float(original_arp) * float(index["vs. Prior Period"])
        before_arp_int = float(original_arp) + float(how_much_new)
        new_arp = before_arp_int
        original_total_units = float(index["Total Units"])
        new_prior_units = data_per_month["vs Prior Period unit"].mean()
        how_much_new = float(original_total_units) * float(index["vs Prior Period unit"])
        new_total_units_int = float(original_total_units) + float(how_much_new)
        new_total_units = new_total_units_int
        new_total_sales = new_arp * new_total_units
        #new_vs_unit = data_per_month["vs Prior Period unit"].mean()
        additional_month_train = additional_month_train.append([new_brand,
                                                               combined_previous_month,
                                                               new_arp, 
                                                               new_vs_prior_period, 
                                                               new_total_units,
                                                               new_prior_units,
                                                               new_total_sales])
        additional_month_train = additional_month_train.append(train_filled_in_copy.iloc[row])
        
        print("New row values are:")
        print("Brand is:")
        print(new_brand)
        print("New month is")
        print(combined_previous_month)
        print("ARP is")
        print(new_arp)
        print("new prior period is")
        print(new_vs_prior_period)
        print("new total units is")
        print(new_total_units)
        print("New prior units are:")
        print(new_prior_units)
        print("new total sales are")
        print(new_total_sales)
        
        print("Original row is:")
        print(additional_month_train)
        
        print("---------------------------------------------------------------------------")
        
        
#     #If the previous entry is not the same brand
#     elif(data_per_month.iloc[next_row]['Brands'] != train_data.iloc[index]['Brands']):
#         new_brand = filled_in_train_data.iloc[index]['Brands']
#         broken_apart_month = index["Months"].split('/')
#         previous_month = str(int(broken_apart_month[0])- 1)
#         year = broken_apart_month[1]
#         if (previous_month == 0):
#             previous_month = str(12)
#             year = str(int(broken_apart_month[1]) - 1)
#         combined_previous_month = previous_month + "/" + year
#         original_arp = float(index["ARP"])
#         new_vs_prior_period = data_per_month["vs. Prior Period"].mean()
#         how_much_new = float(original_arp) * float(index["vs. Prior Period"])
#         before_arp_int = float(original_arp) + float(how_much_new)
#         new_arp = before_arp_int
#         original_total_units = float(index["Total Units"])
#         new_prior_units = data_per_month["vs Prior Period unit"].mean()
#         how_much_new = float(original_total_units) * float(index["vs Prior Period unit"])
#         new_total_units_int = float(original_total_units) + float(how_much_new)
#         new_total_units = new_total_units_int
#         new_total_sales = new_arp * new_total_units
#         #new_vs_unit = data_per_month["vs Prior Period unit"].mean()
#         additional_month_train = additional_month_train.append([new_brand,
#                                                                combined_previous_month,
#                                                                new_arp, 
#                                                                new_vs_prior_period, 
#                                                                new_total_units,
#                                                                new_prior_units,
#                                                                new_total_sales])
#         additional_month_train = additional_month_train.append(train_data.iloc[index])
        
        
    #Easy case, when the previous row has the same brand, and the month is one back
    else:
        additional_month_train = additional_month_train.append(train_filled_in_copy.iloc[row])
        
        print("Original row is:")
        print(additional_month_train)
        print("---------------------------------------------------------------------------")


#to check all of data
additional_month_train.to_csv('additional_month_train.csv', index=False)

row is: 
0
index is
Brands                  #BlackSeries
Months                       08/2020
ARP                        15.684913
vs. Prior Period           -0.525658
Total Units              1616.339004
vs Prior Period unit       -0.421739
Total Sales ($)         25352.135918
Name: 0, dtype: object
New row values are:
Brand is:
#BlackSeries
New month is
7/2020
ARP is
7.440010937684205
new prior period is
-0.06502848986459497
new total units is
934.6663842909998
New prior units are:
0.26744068756635836
new total sales are
6953.928122210787
Original row is:
               0        ARP        Brands   Months  Total Sales ($)  \
4            NaN  22.679732  #BlackSeries  03/2021    409372.856199   
0   #BlackSeries        NaN           NaN      NaN              NaN   
1         7/2020        NaN           NaN      NaN              NaN   
2             15        NaN           NaN      NaN              NaN   
3      -0.065028        NaN           NaN      NaN              NaN   
..        

New row values are:
Brand is:
101 Cannabis Co.
New month is
11/2019
ARP is
0.0
new prior period is
-0.06502848986459497
new total units is
0.0
New prior units are:
0.26744068756635836
new total sales are
0.0
Original row is:
               0        ARP            Brands   Months  Total Sales ($)  \
4            NaN  22.679732      #BlackSeries  03/2021    409372.856199   
0   #BlackSeries        NaN               NaN      NaN              NaN   
1         7/2020        NaN               NaN      NaN              NaN   
2             15        NaN               NaN      NaN              NaN   
3      -0.065028        NaN               NaN      NaN              NaN   
..           ...        ...               ...      ...              ...   
3      -0.065028        NaN               NaN      NaN              NaN   
4            0.0        NaN               NaN      NaN              NaN   
5       0.267441        NaN               NaN      NaN              NaN   
6            0.0        N

New row values are:
Brand is:
101 Cannabis Co.
New month is
3/2020
ARP is
33.587907532448654
new prior period is
-0.06502848986459497
new total units is
538.1144113344869
New prior units are:
0.26744068756635836
new total sales are
18074.137089780786
Original row is:
               0        ARP            Brands   Months  Total Sales ($)  \
4            NaN  22.679732      #BlackSeries  03/2021    409372.856199   
0   #BlackSeries        NaN               NaN      NaN              NaN   
1         7/2020        NaN               NaN      NaN              NaN   
2             15        NaN               NaN      NaN              NaN   
3      -0.065028        NaN               NaN      NaN              NaN   
..           ...        ...               ...      ...              ...   
3      -0.065028        NaN               NaN      NaN              NaN   
4     538.114411        NaN               NaN      NaN              NaN   
5       0.267441        NaN               NaN      NaN   

New row values are:
Brand is:
101 Cannabis Co.
New month is
7/2020
ARP is
32.1613631342066
new prior period is
-0.06502848986459497
new total units is
1759.2998164760843
New prior units are:
0.26744068756635836
new total sales are
56581.48025963038
Original row is:
               0        ARP            Brands   Months  Total Sales ($)  \
4            NaN  22.679732      #BlackSeries  03/2021    409372.856199   
0   #BlackSeries        NaN               NaN      NaN              NaN   
1         7/2020        NaN               NaN      NaN              NaN   
2             15        NaN               NaN      NaN              NaN   
3      -0.065028        NaN               NaN      NaN              NaN   
..           ...        ...               ...      ...              ...   
3      -0.065028        NaN               NaN      NaN              NaN   
4    1759.299816        NaN               NaN      NaN              NaN   
5       0.267441        NaN               NaN      NaN     

-0.06502848986459497
new total units is
255.42796273920447
New prior units are:
0.26744068756635836
new total sales are
9347.42889814723
Original row is:
               0        ARP            Brands   Months  Total Sales ($)  \
4            NaN  22.679732      #BlackSeries  03/2021    409372.856199   
0   #BlackSeries        NaN               NaN      NaN              NaN   
1         7/2020        NaN               NaN      NaN              NaN   
2             15        NaN               NaN      NaN              NaN   
3      -0.065028        NaN               NaN      NaN              NaN   
..           ...        ...               ...      ...              ...   
3      -0.065028        NaN               NaN      NaN              NaN   
4     255.427963        NaN               NaN      NaN              NaN   
5       0.267441        NaN               NaN      NaN              NaN   
6    9347.428898        NaN               NaN      NaN              NaN   
19           NaN  32.

...

New row values are:
Brand is:
Butter Brand
New month is
6/2020
ARP is
19.61022077322002
new prior period is
-0.06502848986459497
new total units is
3104.3383478277387
New prior units are:
0.26744068756635836
new total sales are
60876.76035567504
Original row is:
                 0        ARP        Brands   Months  Total Sales ($)  \
4              NaN  22.679732  #BlackSeries  03/2021    409372.856199   
0     #BlackSeries        NaN           NaN      NaN              NaN   
1           7/2020        NaN           NaN      NaN              NaN   
2               15        NaN           NaN      NaN              NaN   
3        -0.065028        NaN           NaN      NaN              NaN   
...            ...        ...           ...      ...              ...   
3        -0.065028        NaN           NaN      NaN              NaN   
4      3104.338348        NaN           NaN      NaN              NaN   
5         0.267441        NaN           NaN      NaN              NaN   
6     6

New row values are:
Brand is:
Butter Brand
New month is
10/2020
ARP is
18.73004493508022
new prior period is
-0.06502848986459497
new total units is
871.4325048517696
New prior units are:
0.26744068756635836
new total sales are
16321.969973763156
Original row is:
                 0        ARP        Brands   Months  Total Sales ($)  \
4              NaN  22.679732  #BlackSeries  03/2021    409372.856199   
0     #BlackSeries        NaN           NaN      NaN              NaN   
1           7/2020        NaN           NaN      NaN              NaN   
2               15        NaN           NaN      NaN              NaN   
3        -0.065028        NaN           NaN      NaN              NaN   
...            ...        ...           ...      ...              ...   
3        -0.065028        NaN           NaN      NaN              NaN   
4       871.432505        NaN           NaN      NaN              NaN   
5         0.267441        NaN           NaN      NaN              NaN   
6     

New row values are:
Brand is:
Butter Brand
New month is
2/2021
ARP is
18.734217111594983
new prior period is
-0.06502848986459497
new total units is
193.34255274660117
New prior units are:
0.26744068756635836
new total sales are
3622.121360064831
Original row is:
                 0        ARP        Brands   Months  Total Sales ($)  \
4              NaN  22.679732  #BlackSeries  03/2021    409372.856199   
0     #BlackSeries        NaN           NaN      NaN              NaN   
1           7/2020        NaN           NaN      NaN              NaN   
2               15        NaN           NaN      NaN              NaN   
3        -0.065028        NaN           NaN      NaN              NaN   
...            ...        ...           ...      ...              ...   
3        -0.065028        NaN           NaN      NaN              NaN   
4       193.342553        NaN           NaN      NaN              NaN   
5         0.267441        NaN           NaN      NaN              NaN   
6     

New row values are:
Brand is:
Caldera
New month is
5/2020
ARP is
0.0
new prior period is
-0.06502848986459497
new total units is
0.0
New prior units are:
0.26744068756635836
new total sales are
0.0
Original row is:
                 0        ARP        Brands   Months  Total Sales ($)  \
4              NaN  22.679732  #BlackSeries  03/2021    409372.856199   
0     #BlackSeries        NaN           NaN      NaN              NaN   
1           7/2020        NaN           NaN      NaN              NaN   
2               15        NaN           NaN      NaN              NaN   
3        -0.065028        NaN           NaN      NaN              NaN   
...            ...        ...           ...      ...              ...   
3        -0.065028        NaN           NaN      NaN              NaN   
4              0.0        NaN           NaN      NaN              NaN   
5         0.267441        NaN           NaN      NaN              NaN   
6              0.0        NaN           NaN      NaN   

KeyboardInterrupt: 

In [ ]:
#yearly average for each brand
#split
#yearly average


3. Run some basic statistics on your variables including correlations with labels and report findings - Particularly once you employ PCA and other ‘black box’ methods, the descriptive power of any of your features will effectively disappear. Still you want to report out meaningful correlations toCookies to help them flag key indicators they can employ (this step will also be helpful for you in flagging potential co-linearities).

In [ ]:
hd_data["ARP"].hist()
plt.show()

4. Create additional data feature extraction plan and implement a comprehensive pipeline to execute it - Determine and execute a plan to process your data for modeling and then implement a pipeline to execute it. Specifically:
    1. Determine which fields to retain and which to drop.
    2. For those you retain, determine a categorization strategy
    3. Determine an imputation strategy (you should choose more than one imputation method depending on the specifics of your data
    4. Augment at least one feature, ideally a feature cross, or non-linear transition e.
        Determine a strategy for scaling features

5. Implement a single pipeline to execute this transformation

6. Document your data strategy in your report. Provide an explanation or justification for why you chose the data you did, and also detail any experiments you ran and the results

7. Implement a basic Linear Regression predictive model - With your newly pipelined data find and interpret important features (e.g. using regression and associated p-values). If there are any collinearities be careful when incorporating them into the regression.

8. Implement Principle Component Analysis (PCA) - Since your resulting dataframe is likely to be high-dimensionality, employ PCA to reduce the complexity of your dataframe

9. Employ an ensemble method to your predictive model exercise - Leverage an ensemble learning method to generate an optimized prediction model

10. Cross-Validate your training results - Employ K-Fold Cross-validation to your training regimen for both ensemble and single regression models. (Optional: employ a stratifiedshufflesplit as well to ensure equitable distribution along a key parameter)

11. Employ a GridSearch method to optimize your parameters - Leverage gridsearch or an equivalent parameter tuning approach to optimize parameters to your predictive model (Note: you can likely merge the gridsearch and cross-validation steps)

12. Experiment with your own custom models and report out your highest performing model - For this part of the project you have free range to employ any of the tools you’ve learned in class, along with any additional tools or techniques you research independently to see how you can do.